# DC-DC Step-up Converter for 6 - 9 - 12 V from 4-cell NiMH Battery
**Open Hardware Project Design Decisions and Background**

## 1. Input Filter for Boost Converter

### Filter Inductor Selection

We basically take the same 4.7 uH/2A shielded model we also use for the DC/DC boost converter (see below): 
* http://www.mouser.de/ProductDetail/EPCOS-TDK/B82472G6472M000/

We follow the recommendations from http://www.ti.com/lit/an/snva489c/snva489c.pdf.

So the parameters of this inductor are given.


### Filter Capacitor Selection

1. Make sure resonance frequency is at least one decade below switching frequency
$$ C_{fa} = \frac {C_{IN}} {C_{IN}L_f(2 \pi f_S/10)^2-1}$$
2. Ensure proper attenuation of the EMI filter
$$C_{fb} = \frac {1}{L_f} \left( \frac {10^{IAttI_{dB}/40}}{2 \pi f_S} \right)^2$$


In [11]:
import math

C_in = 10 * 10**-6 # 10 uF
L = 4.7 * 10**-6 # 4.7 uH
f_S = 1.3 * 10**6 # 1.3 MHz
Attenuation = 90 # dB

C_fa = C_in / (C_in * L * (2 * math.pi * f_S/10)**2 -1)
C_fb = 1/L * ( 10**(Attenuation/40)/(2 * math.pi * f_S) )**2

C_f = max(C_fa, C_fb )
print 'C_f >= %.3f uF' % (C_f * 10**6)

C_f >= 31.890 uF


### Damping Capacitor Selection

$$ C_d \geq 4 \times C_{IN}$$

ESR:

$$ ESR_d \approx \sqrt{L_f/C_{IN}} $$

In [36]:
C_d = 4 * C_in
ESR_d = math.sqrt(L/C_in)
print '%.3f uF' % (C_d * 10**6)
print '%.3f ESR' % ESR_d

40.000 uF
0.686 ESD


## 2. Output Filter for Boost Converter

According to http://www.aimtec.com/site/Aimtec/files/documents/ApplicationNotes/a016e%20-%20reduction%20of%20output%20ripple%20&%20noise.pdf, 

Minimum capacitor value:

$$(V_{max-ripple}/V_{converter-ripple}) = \frac {XC}{XC + XL}$$

with

$$XC = \frac {1}{2 * \pi * f * C}$$

$$XL = 2 * \pi * f *L$$

$$f = Switching\; frequency\; of\; converter$$
$$C = Filter\; capacitance$$
$$L = Filter\; Inductance$$


In [13]:
V_max_ripple = 5 * 10**-3 # 10mV, just an estimate
V_converter_ripple = 800 * 10**-3 # 600mV, just an estimate
f = 1.3 * 10**6
L = 4.7 * 10**-6

XL = 2 * math.pi * f * L

# XC/(XC + XL) = V_max_ripple / V_converter_ripple
# XC = (V_max_ripple * (XC + XL)) / V_converter_ripple 
# XC * V_converter_ripple  = V_max_ripple * XC + V_max_ripple * XL
# XC(V_converter_ripple - V_max_ripple) = V_max_ripple * XL
XC = V_max_ripple * XL / (V_converter_ripple - V_max_ripple)

# XC = 1 / (2 * math.pi * f * C)
# C * XC = 1 / (2 * math.pi * f) 
C = 1 / (2 * math.pi * f * XC) 

print 'XC = %.3f Ohm' % XC
print 'XL = %.3f Ohm' % XL
print 'C_min = %.3f uF' % (C * 10**6)

XC = 0.241 Ohm
XL = 38.390 Ohm
C_min = 0.507 uF


## 3. Boost Converter Components

### Voltage Divider for  Output Voltage Setting

See http://www.mouser.com/ds/2/761/down-766913.pdf

$$ R_1 = R_2 \left ( \frac {V_{OUT}}{1.25V} - 1 \right ) $$

In [20]:
V_out = 12
R2 = 50 * 10**3 # 50k

for v in [12, 9, 6]:
    R1 = R2*(v/1.25 -1)
    print 'R1 for %i V_out: %.2f kOhm' % (v, R1/10**3)

R1 for 12 V_out: 430.00 kOhm
R1 for 9 V_out: 310.00 kOhm
R1 for 6 V_out: 190.00 kOhm


However, we want to achieve the resistance for the lower output voltage by adding additional resistors parallel to R1.

So 

$$ R_1 = \frac {R_{1a} * R_{1b}}{R_{1a} + R_{1b}}$$

where 
$$ R_{1a} = Resistor\; for\; V_{out} = 12 V => 430k $$

So rearranged to compute R1b:

$$ R_{1b} = \frac {R_1*R_{1a}}{R_{1a} - R_1}$$

In [21]:
R1a = 430 * 10**3
for R1 in [310*10**3, 190*10**3]:
    R1b = (R1 * R1a)/(R1a - R1)
    print 'For R1 = %.2f kOhm: R1a = %.2f kOhm, R1b = %.2f kOhm' % (R1/10**3, R1a/10**3,R1b/10**3) 

For R1 = 310.00 kOhm: R1a = 430.00 kOhm, R1b = 1110.00 kOhm
For R1 = 190.00 kOhm: R1a = 430.00 kOhm, R1b = 340.00 kOhm


So we choose 
* R1b = 1 MOhm for 9 V

and 

* R1b = 330 kOhm for 6 V.

### Inductor Selection

See p. 10 of the SC4503 datasheet, http://www.mouser.com/ds/2/761/down-766913.pdf

The inductor should be chosen such that the ripple current ΔI will be between 0.35A and 0.6A.

$$ L = \frac {V_{IN}} {f \Delta I_L} \left (1 - \frac {V_{IN}} {V_{OUT} + V_D} \right) $$

$$ \Delta I_L = \frac {V_{IN}} {f L} \left (1 - \frac {V_{IN}} {V_{OUT} + V_D} \right) $$

We want to use the same 4.7 uH/2A shielded model we also use for the filters: 
* http://www.mouser.de/ProductDetail/EPCOS-TDK/B82472G6472M000/

In the following, we compute whether this is a good choice.

In [10]:
delta_I_L_min = 0.35 # A
delta_I_L_max = 0.6 # A
f = 1.3 * 10**6 # 1.3 MHz
V_in_min = 4.0
V_in_nominal = 4.8
V_in_max = 6
V_out = 12
# Diode: http://cdn-reichelt.de/documents/datenblatt/A400/SS12L_SS13L_SS14L-TSC.pdf
V_D = 0.55 # V
L = 4.7 * 10**-6 # 4.7 uH

def delta_I_L(V_in, f, L, V_out, V_D):
    i = (V_in / (f * L)) * (1 - (V_in/(V_out + V_D)))
    return i

for v_out in [12, 9, 6]:
    print 'V_out = %i V' %v_out
    for v in [V_in_max, V_in_nominal, V_in_min]:
        print '\tV_in = %.1f V, delta_I = %.3f A' % (v, delta_I_L(v, f, L, v_out, V_D))


V_out = 12 V
	V_in = 6.0 V, delta_I = 0.513 A
	V_in = 4.8 V, delta_I = 0.485 A
	V_in = 4.0 V, delta_I = 0.446 A
V_out = 9 V
	V_in = 6.0 V, delta_I = 0.365 A
	V_in = 4.8 V, delta_I = 0.391 A
	V_in = 4.0 V, delta_I = 0.380 A
V_out = 6 V
	V_in = 6.0 V, delta_I = 0.082 A
	V_in = 4.8 V, delta_I = 0.210 A
	V_in = 4.0 V, delta_I = 0.255 A
